In [1]:
!pip install bs4
!pip install pandas
!pip install numpy
!pip install matplotlib
!pip install matplotlib.pyplot
!pip install dateparser
!pip install --user -U nltk
!pip install pystemmer
!pip install langdetect
!pip install pymorphy2

     |████████████████████████████████| 9.2 MB 552 kB/s eta 0:00:01
     |████████████████████████████████| 4.6 MB 11.1 MB/s eta 0:00:01
  Using cached cycler-0.11.0-py3-none-any.whl (6.4 kB)
     |████████████████████████████████| 1.2 MB 10.9 MB/s eta 0:00:01
     |████████████████████████████████| 300 kB 12.5 MB/s eta 0:00:01
ERROR: Could not find a version that satisfies the requirement matplotlib.pyplot (from versions: none)
ERROR: No matching distribution found for matplotlib.pyplot
Requirement already up-to-date: nltk in /home/aitugan/.local/lib/python3.8/site-packages (3.8.1)


In [1]:
import requests
from bs4 import BeautifulSoup
import re
import string
import dateparser
import math
from collections import defaultdict
import pymorphy2
import Stemmer
from nltk.tokenize import sent_tokenize, word_tokenize
import nltk
nltk.download('punkt')


[nltk_data] Downloading package punkt to /home/aitugan/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

# Parse addresses

In [2]:
def parse_addresses_links():
  url = 'https://www.akorda.kz/ru/addresses' #should be 27 addresses
  pages_num = 3
  addresses_links = {}
  for page in range(1, pages_num+1):
    response = requests.get(url+"?page="+str(page))

    if response.status_code == 200:
      soup = BeautifulSoup(response.content, 'html.parser')

      card_divs = soup.find_all("div", "card")

      for card in card_divs:
        view_div = card.find("div", "view")
        a_tag = view_div.find('a')

        mt3_div = card.find("div", "mt-3")
        h5_tag = mt3_div.find("h5", "mt-3")

        if a_tag:
          link = "https://www.akorda.kz" + a_tag['href']
          addresses_links[h5_tag.get_text()] = link

    else:
      print(f"Failed to scrape the website. Status code: {response.status_code}")

  return addresses_links

In [3]:
def clean_text(text):
  characters_to_remove = ['«', '»', '“', '”', '•', '\xa0', '\r','\t', '…', '–','—','№','0','1','2','3','4','5','6','7','8','9','„','‟']
  pattern = '[' + re.escape(''.join(characters_to_remove)) + ']'
  text = re.sub(pattern, ' ', text)
  return text

def tokenize_words(text):
  text = text.translate(str.maketrans('', '', string.punctuation))
  text = text.lower()
  text = [word.strip() for word in text.split(" ") if word and word.strip()]

  return text

def format_date(date_string):
    date_object = dateparser.parse(date_string, languages=['ru'])
    formatted_date = date_object.strftime("%d/%m/%Y")
    return formatted_date

def contains_kazakh_letters(text):
    kazakh_letters_pattern = r'[әіңғүұқөһӘІҢҒҮҰҚӨҺ]'
    matches = re.findall(kazakh_letters_pattern, text, re.IGNORECASE)
    return bool(matches)

def parse_addresses(addresses_links, isCleaned=False, isTokenized=False):
  pages = {}
  for date, link in addresses_links.items():
    response = requests.get(link)

    date=format_date(date)

    if response.status_code == 200:
      soup = BeautifulSoup(response.content, 'html.parser')
      outer_div = soup.find("div", "mt-5")
      article_div = outer_div.find("article")

      p_tags = article_div.find_all('p')

      for p in p_tags:
        text = p.get_text()
        if contains_kazakh_letters(text):
          continue
        if isCleaned: text = clean_text(text)
        if isTokenized: text = tokenize_words(text)

        if len(text) == 0: continue

        if date in pages:
          pages[date] += text+" "
        else:
          pages[date] = text

    else:
      print(f"Failed to scrape the website. Status code: {response.status_code}")
  return pages

In [4]:
import os
import json
def save_data_to_json(title, data):
  directory = f'../addresses'
  os.makedirs(directory, exist_ok=True)
  title = title.replace('"', '')
  title = title.replace('/', '_')
  file_path = os.path.join(directory, f'{title}.json')
  with open(file_path, 'w', encoding='utf-8') as json_file:
      json.dump(data, json_file, ensure_ascii=False)

In [5]:
addresses_links = parse_addresses_links()
pages = parse_addresses(addresses_links, True)
save_data_to_json("addresses", pages)

# TF-IDF

### Read data from json

In [6]:
json_file_path = "../addresses/addresses.json"
data = {}
if os.path.exists(json_file_path):
    with open(json_file_path, 'r') as json_file:
        data = json.load(json_file)


In [7]:
sent_tokenized_page = {}
for date, page in pages.items():
  sentence_tokens = sent_tokenize(page)
  for i, sentence in enumerate(sentence_tokens):
    sentence = sentence.translate(str.maketrans('', '', string.punctuation))
    sentence = sentence.lower()

  if date in sent_tokenized_page:
    sent_tokenized_page[date] += sentence_tokens
  else:
    sent_tokenized_page[date] = sentence_tokens

print(sent_tokenized_page)

{'01/09/2023': ['Уважаемые соотечественники!', 'Уважаемые депутаты и члены Правительства!', 'В соответствии со статьей    Конституции Республики Казахстан объявляю вторую сессию Парламента VIII созыва открытой.', 'Уважаемые депутаты!', 'Поздравляю всех с открытием очередной сессии и желаю успехов в вашей ответственной деятельности!', 'После весенних выборов количество партий в Парламенте увеличилось, существенно изменился и состав депутатов.', 'Фракции политических партий и депутаты-одномандатники активно включились в работу, инициируя много актуальных законопроектов и поднимая важные вопросы развития страны.', 'Большую работу парламентарии проводили и в летнее время.', 'Всего за два месяца они посетили свыше      населенных пунктов и встретились с избирателями, ознакомившись с ситуацией на местах.', 'Выражаю всем искреннюю признательность за плодотворную деятельность.', 'Думаю, что во время новой сессии темп работы будет еще выше.', 'Дорогие соотечественники!', 'Как вам известно, свое

In [8]:
word_tokenized_page = {}
for date, page in sent_tokenized_page.items():
  for sentence in page:
    word_tokens = word_tokenize(sentence)
    if date in word_tokenized_page:
      word_tokenized_page[date].append(word_tokens)
    else:
      word_tokenized_page[date] = [word_tokens]
print(word_tokenized_page)


{'01/09/2023': [['Уважаемые', 'соотечественники', '!'], ['Уважаемые', 'депутаты', 'и', 'члены', 'Правительства', '!'], ['В', 'соответствии', 'со', 'статьей', 'Конституции', 'Республики', 'Казахстан', 'объявляю', 'вторую', 'сессию', 'Парламента', 'VIII', 'созыва', 'открытой', '.'], ['Уважаемые', 'депутаты', '!'], ['Поздравляю', 'всех', 'с', 'открытием', 'очередной', 'сессии', 'и', 'желаю', 'успехов', 'в', 'вашей', 'ответственной', 'деятельности', '!'], ['После', 'весенних', 'выборов', 'количество', 'партий', 'в', 'Парламенте', 'увеличилось', ',', 'существенно', 'изменился', 'и', 'состав', 'депутатов', '.'], ['Фракции', 'политических', 'партий', 'и', 'депутаты-одномандатники', 'активно', 'включились', 'в', 'работу', ',', 'инициируя', 'много', 'актуальных', 'законопроектов', 'и', 'поднимая', 'важные', 'вопросы', 'развития', 'страны', '.'], ['Большую', 'работу', 'парламентарии', 'проводили', 'и', 'в', 'летнее', 'время', '.'], ['Всего', 'за', 'два', 'месяца', 'они', 'посетили', 'свыше', 'на

In [9]:
morph = pymorphy2.MorphAnalyzer()
morphed_words_no_ending = {}
stemmer = Stemmer.Stemmer('russian')

for date, page in word_tokenized_page.items():
  for sentence in page:
    for i in range(len(sentence)):
      first_tag = morph.parse(sentence[i].lower())[0]
      second_tag = morph.parse(sentence[i-1].lower())[0]
      if first_tag.tag.POS == 'NOUN' and (second_tag.tag.POS == 'ADJF' or second_tag.tag.POS == 'ADJS'):

        cut_adj = stemmer.stemWord(sentence[i-1].lower())
        cut_noun = stemmer.stemWord(sentence[i].lower())

        normal_noun_tag = morph.parse(first_tag.normal_form)[0].tag
        normal_noun = first_tag.normal_form
        normal_adj = morph.parse(second_tag.normal_form)[0]

        if normal_noun_tag.gender is not None:
          if normal_noun_tag.gender == 'masc' and normal_adj.inflect({'masc'}):
            normal_adj = normal_adj.inflect({'masc'}).word
          elif normal_noun_tag.gender == 'femn' and normal_adj.inflect({'femn'}):
            normal_adj = normal_adj.inflect({'femn'}).word
          elif normal_noun_tag.gender == 'neut' and normal_adj.inflect({'neut'}):
            normal_adj = normal_adj.inflect({'neut'}).word
          else:
            normal_adj = morph.parse(second_tag.normal_form)[0].word
        else:
          normal_adj = morph.parse(second_tag.normal_form)[0].word


        if date in morphed_words_no_ending:
          morphed_words_no_ending[date].append([cut_adj+" "+cut_noun, normal_adj+" "+normal_noun])
        else:
          morphed_words_no_ending[date] = [[cut_adj+" "+cut_noun, normal_adj+" "+normal_noun]]

print(morphed_words_no_ending)

{'01/09/2023': [['уважа соотечественник', 'уважаемый соотечественник'], ['уважа депутат', 'уважаемый депутат'], ['втор сесс', 'второй сессия'], ['уважа депутат', 'уважаемый депутат'], ['очередн сесс', 'очередной сессия'], ['ответствен деятельн', 'ответственная деятельность'], ['весен выбор', 'весенний выборы'], ['политическ парт', 'политическую партия'], ['актуальн законопроект', 'актуальный законопроект'], ['важн вопрос', 'важный вопрос'], ['больш работ', 'большая работа'], ['летн врем', 'летнее время'], ['искрен признательн', 'искренняя признательность'], ['плодотворн деятельн', 'плодотворная деятельность'], ['нов сесс', 'новая сессия'], ['дорог соотечественник', 'дорогой соотечественник'], ['ежегодн послан', 'ежегодное послание'], ['хорош традиц', 'хорошая традиция'], ['особ смысл', 'особый смысл'], ['всех ветв', 'всю ветвь'], ['ключев направлен', 'ключевым направление'], ['среднесрочн период', 'среднесрочный период'], ['конкретн поручен', 'конкретное поручение'], ['нов задач', 'нов

In [10]:
def count_word_tf_by_roots(roots):
  word_tf = defaultdict(lambda: defaultdict(list))
  for date, phrases in roots.items():
    count = {}
    for phrase in phrases:
      if (phrase[0],phrase[1]) in count:
        count[(phrase[0],phrase[1])] += 1
      else:
        count[(phrase[0],phrase[1])] = 1

    total = len(page)
    for phrase, cnt in count.items():
      word_tf[date][phrase[0]] = [count[phrase]/total, phrase[1]]

  return word_tf

d = count_word_tf_by_roots(morphed_words_no_ending)
for k, v in d.items():
  print(k,v)


01/09/2023 defaultdict(<class 'list'>, {'уважа соотечественник': [0.0012330456226880395, 'уважаемый соотечественник'], 'уважа депутат': [0.002466091245376079, 'уважаемый депутат'], 'втор сесс': [0.0012330456226880395, 'второй сессия'], 'очередн сесс': [0.0012330456226880395, 'очередной сессия'], 'ответствен деятельн': [0.0012330456226880395, 'ответственная деятельность'], 'весен выбор': [0.0012330456226880395, 'весенний выборы'], 'политическ парт': [0.002466091245376079, 'политическую партия'], 'актуальн законопроект': [0.0012330456226880395, 'актуальный законопроект'], 'важн вопрос': [0.007398273736128237, 'важный вопрос'], 'больш работ': [0.0036991368680641184, 'большая работа'], 'летн врем': [0.0012330456226880395, 'летнее время'], 'искрен признательн': [0.0012330456226880395, 'искренняя признательность'], 'плодотворн деятельн': [0.0012330456226880395, 'плодотворная деятельность'], 'нов сесс': [0.0012330456226880395, 'новая сессия'], 'дорог соотечественник': [0.002466091245376079, '

In [11]:
def count_word_idf_by_roots(roots):
  word_cnt = defaultdict(int)

  for date, phrases in roots.items():
    phrases_list = [(phrase[0],phrase[1]) for phrase in phrases]
    phrases_set = set(phrases_list)
    for phrase in phrases_set:
      word_cnt[phrase] += 1

  word_idf = defaultdict(list)
  for phrase, doc_freq in word_cnt.items():
    word_idf[phrase[0]] = [math.log(len(roots) / word_cnt[phrase]), phrase[1]]

  return word_idf
d = count_word_idf_by_roots(morphed_words_no_ending)
for k, v in d.items():
  print(k,v)


экологическ ауд [3.295836866004329, 'экологический аудит']
персональн ответствен [1.0986122886681098, 'персональная ответственность']
экономическ развит [0.6567795363890705, 'экономическое развитие']
внутристранов ценност [3.295836866004329, 'внутристрановая ценность']
особ рол [2.1972245773362196, 'особую роль']
национальн безопасн [0.5232481437645479, 'национальная безопасность']
дальн газификац [3.295836866004329, 'дальнейшая газификация']
эффективн работ [1.9095425048844386, 'эффективная работа']
активн конкуренц [3.295836866004329, 'активная конкуренция']
необходим решен [3.295836866004329, 'необходимое решение']
цен бумаг [0.9932517730102834, 'ценная бумага']
стратегическ проект [2.1972245773362196, 'стратегический проект']
эт проект [2.1972245773362196, 'этот проект']
полноцен доступ [2.6026896854443837, 'полноценный доступ']
четк определен [3.295836866004329, 'чёткое определение']
жарк месяц [3.295836866004329, 'жаркий месяц']
летн врем [3.295836866004329, 'летнее время']
полн 

In [12]:
def calculate_tf_idf_by_roots(roots, words_tf, words_idf):
  word_tf_idf_by_date={}
  # print(words_tf.items())
  # print(words_idf)

  for date, phrases in roots.items():
    word_tf_idf = {}
    # print(words_tf[date])
    for phrase in phrases:
      # if phrase == 'уязвим категор' or phrase == 'синтетическ наркотик' or phrase == 'электоральн цикл':
      #   print(phrase, words_tf[date][phrase], words_idf[phrase])
      if phrase[0] in words_tf[date] and phrase[0] in words_idf:
        word_tf_idf[(phrase[0],phrase[1])] = words_tf[date][phrase[0]][0] * words_idf[phrase[0]][0]
      else:
        # print(phrase, "in word_tf: ", phrase[0] in words_tf)
        # print(phrase, "in word_idf: ", phrase[0] in words_idf)
        break
    print()
    sorted_word_tf_idf_in_doc = sorted([(item[0][1],item[1]) for item in word_tf_idf.items()], key=lambda item: item[1], reverse=True)
    word_tf_idf_by_date[date] = sorted_word_tf_idf_in_doc[:25]

  return word_tf_idf_by_date


# Main running block

In [ ]:
def main():
    words_tf = count_word_tf_by_roots(morphed_words_no_ending)
    words_idf = count_word_idf_by_roots(morphed_words_no_ending)
    tf_idf = calculate_tf_idf_by_roots(morphed_words_no_ending, words_tf, words_idf)
    save_data_to_json("tf_idf",tf_idf)

main()